In [ ]:
from pandas import DataFrame
import matplotlib.pyplot as plt
from DATA225utils import make_connection, dataframe_query

%matplotlib inline

In [ ]:
conn = make_connection(config_file='stock-prices.ini')

In [ ]:
def compute_moving_average(conn, days, label):
    """
    @cursor the database cursor
    @count the number of days for the moving average
    @label label for the moving average
    """
    _, df = dataframe_query(conn,
        f'SELECT days_ago, price, '
        f'       CASE WHEN ROW_NUMBER() OVER (ORDER BY days_ago) >= {days} '
        f'           THEN AVG(price) OVER (ORDER BY days_ago '
        f'                                 ROWS BETWEEN {days - 1} PRECEDING '
        f'                                 AND CURRENT ROW) '
        f'           ELSE NULL '
        f'       END AS {label} '
        f'FROM recent_prices '
        f'ORDER BY days_ago'
    )
    
    return df

In [ ]:
plt.figure(figsize=(15, 10))

first = True

for days in [3, 5, 10]:
    graph_label = f'{days}_day_moving_average'
    
    df = compute_moving_average(conn, days, graph_label)
    display(df)        

    rows = df.values.tolist()
    xs   = [row[0] for row in rows]
    ys   = [row[1] for row in rows]
    avgs = [row[2] for row in rows]
    
    # Initialize the graph.
    if first:
        plt.xticks(xs)
        plt.plot(xs, ys, linewidth=5)
        plt.title('Moving Average of Stock Prices')
        plt.xlabel('Days ago')
        plt.ylabel('Price')
        first = False

    # Plot the moving average line.
    plt.plot(xs[days - 1:], avgs[days - 1:], label=graph_label)
    
plt.legend()
plt.show()

In [ ]:
conn.close()

#### (c) 2023 by Ronald Mak